In [1859]:
import gymnasium as gym
import skyscraper
import numpy as np
from sklearn.preprocessing import StandardScaler
from collections import defaultdict
import torch
import torch.nn as nn
import torch.optim as optim
import random
import itertools

# ex5


In [1860]:
trajectories = np.loadtxt("powered_flight.txt", dtype=int)  # Reads as integers
trajectories = trajectories - [1, 1, 0, 0, 1, 1]


In [1861]:
#Transistion function

def transition_function(trajectories):
    transition_dict = {}

    for step in trajectories:
        state = (step[0], step[1])  # Current state (assuming 2D state)
        action = step[2]  # Action taken
        new_state = (step[4], step[5])  # Next state (assuming 2D state)

        # Store multiple transitions per (state, action) pair
        if (state, action) not in transition_dict:
            transition_dict[(state, action)] = []
        
        transition_dict[(state, action)].append(new_state)

    return transition_dict

print(transition_function(trajectories))

{((np.int64(17), np.int64(16)), np.int64(1)): [(np.int64(16), np.int64(12))], ((np.int64(3), np.int64(60)), np.int64(1)): [(np.int64(3), np.int64(56))], ((np.int64(11), np.int64(19)), np.int64(2)): [(np.int64(10), np.int64(22))], ((np.int64(16), np.int64(9)), np.int64(2)): [(np.int64(18), np.int64(11))], ((np.int64(7), np.int64(14)), np.int64(1)): [(np.int64(8), np.int64(11))], ((np.int64(2), np.int64(37)), np.int64(1)): [(np.int64(2), np.int64(34))], ((np.int64(17), np.int64(16)), np.int64(2)): [(np.int64(16), np.int64(20))], ((np.int64(4), np.int64(55)), np.int64(1)): [(np.int64(4), np.int64(51))], ((np.int64(3), np.int64(39)), np.int64(2)): [(np.int64(1), np.int64(42))], ((np.int64(2), np.int64(58)), np.int64(2)): [(np.int64(2), np.int64(63))], ((np.int64(2), np.int64(56)), np.int64(2)): [(np.int64(3), np.int64(60))], ((np.int64(1), np.int64(53)), np.int64(1)): [(np.int64(2), np.int64(51))], ((np.int64(9), np.int64(13)), np.int64(2)): [(np.int64(10), np.int64(16))], ((np.int64(18), 

In [1862]:
def reward_function(trajecotries):
    reward_dict = {}

    for step in trajectories:
        state = (step[0], step[1])  # Current state (assuming 2D state)
        action = step[2]  # Action taken
        reward = step[3]

        # Store multiple transitions per (state, action) pair
        if (state, action) not in reward_dict:
            reward_dict[(state, action)] = []
        
        reward_dict[(state, action)].append(reward)

    return reward_dict

print(reward_function(trajectories))

{((np.int64(17), np.int64(16)), np.int64(1)): [np.int64(0)], ((np.int64(3), np.int64(60)), np.int64(1)): [np.int64(0)], ((np.int64(11), np.int64(19)), np.int64(2)): [np.int64(0)], ((np.int64(16), np.int64(9)), np.int64(2)): [np.int64(0)], ((np.int64(7), np.int64(14)), np.int64(1)): [np.int64(0)], ((np.int64(2), np.int64(37)), np.int64(1)): [np.int64(0)], ((np.int64(17), np.int64(16)), np.int64(2)): [np.int64(0)], ((np.int64(4), np.int64(55)), np.int64(1)): [np.int64(0)], ((np.int64(3), np.int64(39)), np.int64(2)): [np.int64(0)], ((np.int64(2), np.int64(58)), np.int64(2)): [np.int64(0)], ((np.int64(2), np.int64(56)), np.int64(2)): [np.int64(0)], ((np.int64(1), np.int64(53)), np.int64(1)): [np.int64(0)], ((np.int64(9), np.int64(13)), np.int64(2)): [np.int64(0)], ((np.int64(18), np.int64(57)), np.int64(2)): [np.int64(0)], ((np.int64(1), np.int64(55)), np.int64(1)): [np.int64(0)], ((np.int64(7), np.int64(10)), np.int64(2)): [np.int64(0)], ((np.int64(3), np.int64(53)), np.int64(2)): [np.int

In [1863]:
env = gym.make('skyscraper/GridWorld-v0')
env2 = gym.make('skyscraper/GridWorld-v0').unwrapped 

In [1864]:
obs, info = env.reset()
print(obs)
obs, _, _, _, _=env.step(1)
print(obs)

{'agent': {'pos': array([13,  5])}}
{'agent': {'pos': array([14.,  8.])}}


/Users/christofferslettebo/anaconda3/envs/inf266/lib/python3.11/site-packages/gymnasium/utils/passive_env_checker.py:134: UserWarning: WARN: The obs returned by the `reset()` method was expecting numpy array dtype to be int32, actual type: int64
  logger.warn(
/Users/christofferslettebo/anaconda3/envs/inf266/lib/python3.11/site-packages/gymnasium/utils/passive_env_checker.py:158: UserWarning: WARN: The obs returned by the `reset()` method is not within the observation space.
  logger.warn(f"{pre} is not within the observation space.")
/Users/christofferslettebo/anaconda3/envs/inf266/lib/python3.11/site-packages/gymnasium/utils/passive_env_checker.py:134: UserWarning: WARN: The obs returned by the `step()` method was expecting numpy array dtype to be int32, actual type: float64
  logger.warn(
/Users/christofferslettebo/anaconda3/envs/inf266/lib/python3.11/site-packages/gymnasium/utils/passive_env_checker.py:158: UserWarning: WARN: The obs returned by the `step()` method is not within th

#Chat kode

In [1865]:
class TransitionModel(nn.Module):
    def __init__(self, input_dim=3):  # (x, y, a) → (x', y')
        super().__init__()
        map = [range(0, 32, 1), range(0, 64, 1)]
        self.label = list(itertools.product(*map))
        self.fc = nn.Sequential(
            nn.Linear(input_dim, 64),
            nn.ReLU(),
            nn.Linear(64, 32*64)
        )

    def forward(self, state_action):
        return self.fc(state_action)

class RewardModel(nn.Module):
    def __init__(self, input_dim=3, output_dim=1):  # (x, y, a) → r
        super().__init__()
        self.fc = nn.Sequential(
            nn.Linear(input_dim, 64),
            nn.ReLU(),
            nn.Linear(64, output_dim)
        )

    def forward(self, state_action):
        return self.fc(state_action)



In [1866]:
def train_model_from_data(recorded_trajectories, transition_model, reward_model, epochs=10, batch_size=32):
    """
    Train the transition and reward models using recorded trajectories.
    
    Parameters:
    - recorded_trajectories: List of (s, a, r, s´) tuples.
    - transition_model: Neural network for predicting next state.
    - reward_model: Neural network for predicting reward.
    - epochs: Number of training iterations.
    - batch_size: Number of samples per training step.
    """
    loss_fn = nn.MSELoss()  # Mean Squared Error for both models
    optimizer_T = optim.Adam(transition_model.parameters(), lr=0.001)
    optimizer_R = optim.Adam(reward_model.parameters(), lr=0.001)
    
    for epoch in range(epochs):
        # Sample a batch of experiences
        for state_x, state_y, action, reward, next_state_x, next_state_y in recorded_trajectories:

        # Convert to PyTorch tensors
            reward = torch.tensor(reward, dtype=torch.float)
            next_state = torch.tensor(
                transition_model.label.index((next_state_x, next_state_y)), dtype=torch.long
                )
            state_action = torch.tensor((state_x, state_y, action), dtype=torch.float)  # (x, y, a)

            # Train transition model
            optimizer_T.zero_grad()
            pred_next_states = transition_model(state_action)
            loss_T = nn.functional.cross_entropy(pred_next_states, next_state)
            loss_T.backward()
            optimizer_T.step()

            # Train reward model
            optimizer_R.zero_grad()
            pred_rewards = reward_model(state_action)
            loss_R = loss_fn(pred_rewards, reward)
            loss_R.backward()
            optimizer_R.step()

        if epoch % 100 == 0:
            print(f"Epoch {epoch}: Loss_T = {loss_T.item()}, Loss_R = {loss_R.item()}")

    print("Model training completed!")



In [1867]:
def eps_greedy(Q, state, action_size, epsilon=0.1):
        """Epsilon-greedy action selection."""
        if np.random.rand() < epsilon:
            return np.random.choice(action_size)  # Explore
        return np.argmax(Q[state][i] for i in range(action_size))  # Exploit

def q_learning(state, action, reward, next_state, Q, alpha, gamma, action_size):
    """Q-learning update rule."""
    best_next_action = np.argmax(Q[next_state[0]][next_state[1]][i] for i in range(action_size))
    print(state, action, next_state, best_next_action)
    Q[state[0]][state[1]][action] += alpha * (reward + gamma * Q[next_state[0]][next_state[1]][best_next_action] - Q[state[0]][state[1]][action])

def update_model(state, action, reward, next_state, transition_model, reward_model):
    train_model_from_data([(state[0], state[1], action, reward, next_state[0], next_state[1])], transition_model, reward_model)

def predict_model(state, action, transition_model, reward_model):
    with torch.no_grad():
        x = torch.tensor((state[0], state[1], action), dtype=torch.float)
        transition_model.eval()
        reward_model.eval()
        new_state = transition_model(x)
        new_state = transition_model.label[torch.argmax((new_state))]
        reward = reward_model(x)

    return reward, new_state

In [1868]:
def dyna_q(env, recorded_trajectories, alpha=0.1, gamma=0.95, epsilon=0.1, planning_steps=10, episodes=500):
    """
    Implements the Dyna-Q reinforcement learning algorithm.
    
    Parameters:
        env: The environment (assumed to follow OpenAI Gym-like API).
        alpha: Learning rate.
        gamma: Discount factor.
        epsilon: Exploration probability.
        planning_steps: Number of simulated updates per real step.
        episodes: Number of episodes to train.

    Returns:
        Q-table (state-action values) and optimal policy.
    """
    state_size = env2.height * env2.width
    action_size = env2.action_space.n
    states = []
    # Initialize Q-table
    Q = np.zeros((env2.height, env2.width, 2), dtype=('float64')  )
    observed_state = []
    for x, y, _, _, a, b   in recorded_trajectories:
        if ([x, y] not in observed_state): observed_state.append([x,y])
        if ([a, b] not in observed_state): observed_state.append([a,b])
    recorded_trajectories = recorded_trajectories
    # Model: Dictionary storing transitions {(state, action): (reward, next_state)}
    transition_model = TransitionModel()
    reward_model = RewardModel()
    train_model_from_data(recorded_trajectories=recorded_trajectories, transition_model=transition_model, reward_model=reward_model)

    # Training loop
    for episode in range(episodes):
        observation, info  = env.reset()
        state = tuple(observation.get("agent").get("pos"))
        if(state not in observed_state): observed_state.append(state)
        action = eps_greedy(Q, state, action_size)
        new_observation, reward, terminated, _, info = env.step(action)
        new_state = tuple(new_observation["agent"]["pos"])
        new_state = (int(new_state[0]), int(new_state[1]))
        print(f"before q learning {new_state}, {action}, {reward}")
        q_learning(state, action, reward, new_state, Q, alpha, gamma, action_size) 
        update_model(state, action, reward, new_state, transition_model, reward_model)
        if(new_state not in observed_state): observed_state.append(new_state)
        state=new_state

        for imaginary_step in range(100):
            imag_state = observed_state[np.random.choice(len(observed_state))]
            imag_action = np.random.choice(action_size)
            print(imag_state, imag_action)
            imag_reward, imag_new_state = predict_model(imag_state, imag_action, transition_model, reward_model)
            q_learning(imag_state, imag_action, imag_reward, imag_new_state, Q=Q, alpha=alpha, action_size=action_size, gamma=gamma)

    # Derive optimal policy from Q-table
    optimal_policy = np.argmax(Q, axis=1)
    return Q, optimal_policy

dyna_q(env=env, recorded_trajectories=trajectories)

/Users/christofferslettebo/anaconda3/envs/inf266/lib/python3.11/site-packages/torch/nn/modules/loss.py:608: UserWarning: Using a target size (torch.Size([])) that is different to the input size (torch.Size([1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch 0: Loss_T = 7.43446159362793, Loss_R = 0.00042435433715581894
Model training completed!
before q learning (13, 5), 0, 0
(np.int64(13), np.int64(5)) 0 (13, 5) 0
Epoch 0: Loss_T = 6.361673355102539, Loss_R = 0.00016843096818774939
Model training completed!
[np.int64(0), np.int64(40)] 1
[np.int64(0), np.int64(40)] 1 (8, 55) 0
[np.int64(8), np.int64(21)] 1
[np.int64(8), np.int64(21)] 1 (8, 55) 0
[np.int64(10), np.int64(17)] 1
[np.int64(10), np.int64(17)] 1 (11, 22) 0
[np.int64(18), np.int64(9)] 0
[np.int64(18), np.int64(9)] 0 (21, 8) 0
[np.int64(4), np.int64(21)] 0
[np.int64(4), np.int64(21)] 0 (8, 55) 0
[np.int64(9), np.int64(4)] 1
[np.int64(9), np.int64(4)] 1 (10, 19) 0
[np.int64(2), np.int64(52)] 0
[np.int64(2), np.int64(52)] 0 (8, 55) 0
[np.int64(5), np.int64(14)] 1
[np.int64(5), np.int64(14)] 1 (7, 26) 0
[np.int64(4), np.int64(54)] 0
[np.int64(4), np.int64(54)] 0 (8, 55) 0
[np.int64(4), np.int64(0)] 1
[np.int64(4), np.int64(0)] 1 (10, 19) 0
[np.int64(9), np.int64(62)] 1
[np.int6

(array([[[ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         ...,
         [-0.30506146, -0.3009029 ],
         [-0.35764542, -0.30571172],
         [ 0.        ,  0.        ]],
 
        [[ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         ...,
         [-0.28077862, -0.31120619],
         [-0.29755217, -0.27118313],
         [-0.27122834, -0.29527307]],
 
        [[ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         ...,
         [-0.2367489 , -0.32713944],
         [-0.25337628, -0.27361402],
         [-0.30272734, -0.22603694]],
 
        ...,
 
        [[ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         ...,
         [ 0.        ,  0.        ],
         [ 0.        ,  0.        ],
         [ 0.        ,  0.        ]],
 
        [[ 0.        ,  0.   